## LIBRERIAS 
## DEPENDENCIES

In [2]:
import pandas as pd
import folium

from geopy.geocoders import Nominatim

In [ ]:
# https://towardsdatascience.com/your-cool-folium-maps-on-the-web-313f9d1a6bcd

## Importar data

In [5]:
colegios = pd.read_csv('./data/data_coles_complete.csv', index_col=0)

In [6]:
colegios

AREA TERRITORIAL  CODIGO CENTRO TIPO DE CENTRO  \
1       Madrid-Oeste       28060646            EEI   
2        Madrid-Este       28063027            EEI   
3         Madrid-Sur       28047460            EEI   
4     Madrid-Capital       28047551            EEI   
5         Madrid-Sur       28044100            EEI   
..               ...            ...            ...   
839     Madrid-Oeste       28030681    CPR PRI-SEC   
840   Madrid-Capital       28009677    CPR PRI-SEC   
841       Madrid-Sur       28029445    CPR PRI-SEC   
842   Madrid-Capital       28076927    CPR PRI-SEC   
843   Madrid-Capital       28014612    CPR INF-SEC   

                                              CENTRO  \
1                                            ACHALAY   
2                                           ACUARELA   
3                                        ADIVINANZAS   
4                                         AGUA DULCE   
5                                           AILANTOS   
..                                               ...   
839                                    SAN MIGUEL II   
840                        SANTA MARIA DEL VALLE CEP   
841  SEMINARIO ARZOBISPAL LA INMACULADA Y SAN DAMASO   
842              STELLA MARIS COLLEGE & PREP. SCHOOL   
843                                      SANTO ANGEL   

                                DOMICILIO                MUNICIPIO  \
1      Avenida De Isabel De Farnesio, 14        Boadilla del Monte   
2           Avenida Del Somorrostro, 193   San Fernando de Henares   
3                  Plaza Duque De Ahumada                 Alcorcón   
4                   Calle De Leñeros, 25                    Madrid   
5            Plaza Duque De Ahumada, S/n                 Valdemoro   
..                                    ...                      ...   
839                Calle Río Guadiana, 2        Boadilla del Monte   
840                Calle De Vitruvio, 14                    Madrid   
841  Carretera Alcorcon-plasencia, K. 67      Rozas de Puerto Real   
842               Calle De Valdesquí, 16                    Madrid   
843      Calle Del Arroyo Fontarrón, 209                    Madrid   

    DISTRITO MUNICIPAL COD. POSTAL   TELEFONO        FAX  \
1                    -       28660  916326518          -   
2                    -       28830  916694580          -   
3                    -       28922  911886061          -   
4               Tetuán       28039  914594049  914594049   
5                    -       28341  918955900  918955900   
..                 ...         ...        ...        ...   
839                  -       28669  916330078  916322527   
840          Chamartín       28006  915612093          -   
841                  -       28649  918610200  918611356   
842    Moncloa-Aravaca       28023  910882353          -   
843          Moratalaz       28030  917721100  917732675   

                                         EMAIL  \
1        eei.achalay.boadilla@educa.madrid.org   
2    eei.acuarela.sanfernando@educa.madrid.org   
3    eei.adivinanzas.alcorcon@educa.madrid.org   
4        eei.aguadulce.madrid@educa.madrid.org   
5      eei.ailantos.valdemoro@educa.madrid.org   
..                                         ...   
839                dtecnica@stmichelsschool.es   
840    direccionvitruvio@santamariadelvalle.es   
841               colegioseminario@rozascs.org   
842           secretaria@stellamariscollege.es   
843          secretaria@santoangelmoratalaz.es   

                                       EMAIL2 TITULARIDAD        TIPO  \
1                        achalay-@hotmail.com     Público    Primaria   
2                                           -     Público    Primaria   
3                                           -     Público    Primaria   
4                                           -     Público    Primaria   
5                 manuelaailantos@hotmail.com     Público    Primaria   
..                                        ...         ...         ...   
839     

In [8]:
resis = pd.read_csv('./data/data_resis_complete.csv')

In [ ]:
for i in range(0, len(resis)):
    

## Limpieza de datos (preprocesado)
## Preprocessing data


In [ ]:
# quitar S/N (sin numero en ciertas direcciones)
calles = []

for i in range(0,len(colegios)):
    if 'S/n' in colegios.iloc[i]['DOMICILIO']:
        calles.append(colegios.iloc[i]['DOMICILIO'].replace(', S/n', ' '))
    else: 
        calles.append(colegios.iloc[i]['DOMICILIO'])

print(len(calles))
colegios['calle'] = calles

## GEOCODING

In [29]:
geolocator = Nominatim(user_agent="example app")

In [10]:
# buscar latitudes y longitudes 

def get_coordinates(df, street_column, postal_code):
    latitudes = []
    longitudes = []
    for i in range(0,len(df)):
        try: 
            x = geolocator.geocode(df.iloc[i][street_column]+', Madrid, '+df.iloc[i][postal_code]).point
            latitudes.append(x[0])
            longitudes.append(x[1])
        except: 
            latitudes.append('N/A')
            longitudes.append('N/A')

    return latitudes, longitudes


In [ ]:
latitudes, longitudes = get_coordinates(colegios, 'calle', 'CODIGO POST.')

In [32]:
colegios['latitudes'] = latitudes
colegios['longitudes'] = longitudes

Hacer lo mismo para las residencias 

In [125]:
latitudes, longitudes = get_coordinates(resis, 'Calle', 'CP')
resis['latitudes'] = latitudes
resis['longitudes'] = longitudes

In [ ]:
# resis.to_csv('./data/data_resis_complete.csv')
# colegios.to_csv('./data/data_coles_complete.csv')

## Dealing with outliers (no los pillaba bien el geocoder- los ponia fuera de madrid)

In [152]:
# changing lat/long of TOPITOS

colegios.replace(38.5465262, 40.6362510467149, inplace=True)
colegios.replace(-0.1344536, -4.003578515877017, inplace=True)

In [163]:
# changing lat/long of Las cumbres

colegios.replace(38.5468246, 40.55409582358531, inplace=True)
colegios.replace(-0.12771876388221354, -3.630698196842926, inplace=True)

In [168]:
# changing lat/long of GRIMM

colegios.replace(36.4635133, 40.36227667986738, inplace=True)
colegios.replace(-5.0413245, -3.5329390312277527, inplace=True)

## Dibujar el Mapa
## Drawing on Map


In [5]:
colegios = pd.read_csv('./data/data_coles_complete.csv')
resis = pd.read_csv('./data/data_resis_complete.csv')

#### map version 1

In [15]:
m = folium.Map(location=[40.380708,-3.741548], prefer_canvas=True)

# optional argument zoom_start=5

In [16]:
for i in range(0,len(resis)):
    try:
        folium.Marker(location=[resis.iloc[i]['latitudes'],resis.iloc[i]['longitudes']], popup=resis.iloc[i]['Residencia'], icon=folium.Icon(color='black', icon_color='#bdd2c1') ).add_to(m)
    except: 
         i = i 

In [17]:
for i in range(0,len(colegios)):
    try:
        folium.CircleMarker(location=[colegios.iloc[i]['latitudes'],colegios.iloc[i]['longitudes']], popup=colegios.iloc[i]['CENTRO'], radius=7, color="#f0985d", fill_color="#f0985d"  ).add_to(m)
    except: 
        i = i 

### colors : #bdd2c1, #596a62, #f0985d

### marker cluster map 

In [170]:
from folium.plugins import MarkerCluster

In [265]:
f = folium.Map(location=[40.380708,-3.741548], prefer_canvas=True)

In [278]:
f.save('dt2_map3.html')

In [266]:
marker_cluster = MarkerCluster(name="Cluster").add_to(f)

In [267]:
for i in range(0,len(colegios)):
    try:
        dist = round(close_dist[i],2)
        if dist <= 5:
            folium.CircleMarker(location=[colegios.iloc[i]['latitudes'],colegios.iloc[i]['longitudes']], popup= ( colegios.iloc[i]['CENTRO']+' Residencia mas cercana a: '+str(dist)+', '+resis.iloc[resi_number[i]]['Residencia']), radius=10, color='green', fill_color="green"  ).add_to(marker_cluster)
        else:
            folium.CircleMarker(location=[colegios.iloc[i]['latitudes'],colegios.iloc[i]['longitudes']], popup= ( colegios.iloc[i]['CENTRO']+' Residencia mas cercana a: '+str(dist)+', '+resis.iloc[resi_number[i]]['Residencia']), radius=10, color='black', fill_color="red"  ).add_to(marker_cluster)
    except: 
        x = i

In [275]:
for i in range(0,len(resis)):
    try:
        name = resis.iloc[i]['Residencia'].upper()+' '+str(number_close_schools[i])+' colegios a 5km o menos.'
        folium.Marker(location=[resis.iloc[i]['latitudes'],resis.iloc[i]['longitudes']], popup=name, icon=folium.Icon(color='black', icon_color='#bdd2c1') ).add_to(f)
    except: 
        x = i

In [276]:
folium.LayerControl().add_to(f)

In [193]:
# '('+resis.iloc[i]['Tipo']+')'

'(Primera Acogida)'

In [277]:
f

# DISTANCE?

In [77]:
from geopy import distance

In [194]:
## Calculate the distance between schools and resis
# find the closest resi to a school

close_dist = list(range(0,len(colegios)))
resi_number = [0] * len(colegios)

for i in range(0, len(colegios)):
    win = 1000000
    for j in range(0, len(resis)):

        lat_resi = resis.iloc[j]['latitudes']
        lon_resi = resis.iloc[j]['longitudes']
        lat_cole = colegios.iloc[i]['latitudes']
        lon_cole = colegios.iloc[i]['longitudes']

        start, end = (lat_resi,lon_resi),(lat_cole,lon_cole)

        try:
            aux = distance.distance(start, end).km

            if aux < win :
                win = aux 
                
                close_dist[i] = aux
                resi_number[i] = j

        except:
            win = win

In [256]:
# close_dist.to_csv('dist_resi_mas_cercana.csv')
# resi_number.to_csv('num_resi_mas_cercana.csv')

In [259]:
## Calculate the distance between schools and resis
# find all resis <= 5 km to a school
close_schools_dist = []
close_schools = []

for p in range(0, len(resis)):

    lat_resi = resis.iloc[p]['latitudes']
    lon_resi = resis.iloc[p]['longitudes']

    close_schools.append([])
    close_schools_dist.append([])

    if math.isnan(lat_resi) == False and math.isnan(lon_resi) == False:

        for q in range(0, len(colegios)):
            
            lat_cole = colegios.iloc[q]['latitudes']
            lon_cole = colegios.iloc[q]['longitudes']

            if lat_cole != 'N/A' and lon_cole != 'N/A':

                start, end = (lat_resi,lon_resi),(lat_cole,lon_cole)
                try: 
                    aux = distance.distance(start, end).km
                except: 
                    print(p,q,start,end)

                if aux <= 5:
                    close_schools[p].append(q)
                    close_schools_dist[p].append(aux)
                else: 
                    continue

            else: continue
    else: 
        continue


1 4888 (40.6148809, -4.013341278551532) (10, nan)
2 4888 (40.2481046, -3.1397113) (10, nan)
4 4888 (40.46569315, -3.6799454650741024) (10, nan)
7 4888 (40.4899445, -3.3481572) (10, nan)
8 4888 (40.759214, -3.7817977) (10, nan)
9 4888 (40.549061550000005, -3.9937888571128304) (10, nan)
10 4888 (40.3455262, -3.8305627) (10, nan)
11 4888 (40.2942901, -3.4426635) (10, nan)
14 4888 (40.4528048, -3.6506067) (10, nan)
15 4888 (40.4350043, -3.7045282) (10, nan)
16 4888 (40.37726385, -3.624554616800947) (10, nan)
17 4888 (40.566672, -3.5042791) (10, nan)
18 4888 (40.3268109, -3.8789307) (10, nan)
20 4888 (40.5745912, -3.9525075) (10, nan)
22 4888 (40.4288625, -4.0613155) (10, nan)
25 4888 (40.461752, -3.772816) (10, nan)
27 4888 (40.438796, -3.6739457) (10, nan)
28 4888 (40.3715037, -3.6885208) (10, nan)
29 4888 (40.2483973, -3.6948228) (10, nan)
30 4888 (40.3230102, -3.763188750759631) (10, nan)
33 4888 (40.4525109, -3.6495747) (10, nan)
34 4888 (40.3965049, -3.7305213) (10, nan)
35 4888 (40.4

In [263]:
number_close_schools = []

for m in range(0, len(resis)):
    number_close_schools.append(len(close_schools[m]))

In [264]:
number_close_schools

[0,
 130,
 0,
 0,
 747,
 0,
 0,
 110,
 6,
 38,
 201,
 38,
 0,
 0,
 677,
 809,
 273,
 21,
 185,
 0,
 72,
 0,
 8,
 0,
 0,
 132,
 0,
 948,
 518,
 29,
 282,
 0,
 0,
 670,
 630,
 124,
 719,
 0,
 655,
 129,
 842,
 890,
 3,
 4,
 114,
 520,
 101,
 0,
 601,
 975,
 0,
 83,
 0,
 301,
 0,
 65,
 0,
 0,
 0,
 0,
 0,
 5,
 0,
 667,
 234,
 206,
 623,
 0,
 0,
 0,
 0,
 0,
 21,
 0,
 0,
 0]

In [261]:
close_schools_dist

[[],
 [2.6556014916135715,
  3.641612443371503,
  4.676485922393543,
  3.7293771962663422,
  1.619435649220986,
  2.537125632229574,
  1.619380297318087,
  1.658770075851239,
  2.6550494106886955,
  2.6556014916135715,
  1.5834977415069147,
  1.658770075851239,
  4.215700760820566,
  4.885657586905465,
  1.619380297318087,
  2.6550494106886955,
  2.4527967477237795,
  2.0747024736175965,
  4.363409244155676,
  3.4581762020186577,
  2.9736488223275663,
  3.455550499870244,
  3.831170414092235,
  1.6996623117274872,
  2.177451362306156,
  0.9683458576366915,
  1.5826660377044324,
  1.315458187842543,
  1.5581088273450197,
  1.9140177070390738,
  4.426744984821669,
  3.742488164171226,
  2.7388436544280887,
  1.3293709430745355,
  3.999318431944248,
  1.6160281281825282,
  3.332991856604115,
  1.9589636765091043,
  1.6882572560831854,
  1.9945664316709175,
  2.631186748953749,
  0.5987276921737181,
  3.5430319778176105,
  2.1761270736140874,
  2.037968204028283,
  4.4129866677649625,
  2.

In [260]:
close_schools

[[],
 [23,
  43,
  85,
  139,
  190,
  232,
  305,
  343,
  355,
  414,
  419,
  421,
  436,
  440,
  516,
  521,
  644,
  683,
  695,
  755,
  788,
  872,
  891,
  932,
  1010,
  1031,
  1051,
  1052,
  1054,
  1181,
  1249,
  1263,
  1279,
  1289,
  1320,
  1365,
  1377,
  1392,
  1398,
  1445,
  1494,
  1499,
  1503,
  1553,
  1593,
  1599,
  1610,
  1627,
  1658,
  1687,
  1782,
  1796,
  1841,
  1951,
  1978,
  1989,
  1999,
  2037,
  2049,
  2071,
  2094,
  2119,
  2267,
  2300,
  2314,
  2337,
  2383,
  2407,
  2427,
  2429,
  2584,
  2588,
  2624,
  2639,
  2669,
  2706,
  2721,
  2766,
  2801,
  2804,
  2832,
  2962,
  2968,
  2985,
  2987,
  3024,
  3033,
  3056,
  3120,
  3142,
  3169,
  3360,
  3480,
  3526,
  3688,
  3789,
  3821,
  3827,
  3896,
  3963,
  3964,
  3984,
  3999,
  4086,
  4090,
  4094,
  4136,
  4171,
  4176,
  4185,
  4202,
  4233,
  4256,
  4342,
  4353,
  4412,
  4426,
  4449,
  4495,
  4519,
  4539,
  4541,
  4695,
  4700,
  4735,
  4751,
  4781,
  4836

In [ ]:
start_dropdown = ipywidgets.Dropdown(options= list(resis.Residencia)
                value = list(resis.Residencia)[0]
                description='start'
                disabled = False

)

end_dropdown = ipywidgets.Dropdown(options= list(colegios.CENTRO)
                value = list(colegios.CENTRO))[0]
                description='end'
                disabled = False
)

In [152]:
distance.distance( , ).km

SyntaxError: invalid syntax (2251552630.py, line 1)